# Using a model to analyze sequences

In this tutorial, we demonstrate how to use the individual classes and functions provided in Selene to make model predictions.

If you want to run this notebook, please start it with `jupyter notebook --NotebookApp.iopub_data_rate_limit=10000000000`.
The Plotly visualization will not render otherwise.
Alternatively, you can ignore the call to `iplot` because the HTML file will be saved to the output directory regardless.

We also provide the equivalent configuration file in `data` which can be used in-place of the individual API functions, so you can see how the two compare.
If you want to run Selene with these files, you can use the 2 methods specified in the Quickstart tutorial (`load_path` and `parse_configs_and_run`). 
Note that Selene does NOT run any visualization functions via the configuration files.
That is, you would use the config files to run variant effect prediction and _in silico_ mutagenesis, get their output files, and then run the visualization-specific sections in this notebook (section headers begin with "Visualizing").

In [1]:
import os

from plotly.offline import download_plotlyjs, init_notebook_mode, iplot

from selene_sdk.predict import AnalyzeSequences
from selene_sdk.sequences import Genome
from selene_sdk.utils import load_features_list
from selene_sdk.utils import NonStrandSpecific
from selene_sdk.utils import DeeperDeepSEA


init_notebook_mode(connected=True)

## Variant effect prediction

First, initialize the `selene.predict.AnalyzeSequences` class. The constructor requires the following as inputs:

- the model architecture (`torch.nn.Module`)
- path to the trained model weights file
- the sequence length on which the model was trained 
- the list of distinct targets/features the model predicts
- optionally, the batch size (default 64) and `use_cuda`, depending on whether CUDA is enabled on your machine

For variant effect prediction in particular, we must specify a specific `Genome` version.
In this case, we are looking at variants whose positions were determined using hg19, so we initialize a `Genome` with the hg19 FASTA file.

For _in silico_ mutagenesis, we only need to pass in the sequence type.
That is, it is sufficient to only specify that we are working with `selene.sequences.Genome`, as opposed to `selene.sequences.Proteome`, as it determines the possible mutations at each position in the sequence.

The first example we present in this notebook is of variant effect prediction:

In [2]:
distinct_features = load_features_list(os.path.join("data", "deepsea_features.txt"))

model_predict = AnalyzeSequences(
    NonStrandSpecific(DeeperDeepSEA(1000, 919)),
    "0611_deeperdeepsea.pth.tar",
    sequence_length=1000,
    features=distinct_features,
    reference_sequence=Genome(
        os.path.join("data", "male.hg19.fasta")),
    use_cuda=True  # update this to False if you do not have CUDA on your machine.
)

In [3]:
variants_output_dir = os.path.join("data", "example_variants")
model_predict.variant_effect_prediction(
    "25k_example_variants.vcf",
    save_data=["abs_diffs"],  # only want to save the absolute diff score data
    output_dir=variants_output_dir)

## Visualizing the absolute difference scores for variant effect prediction

The visualization we provide for variant effect prediction is a Manhattan plot, where the y-axis is the max absolute difference for a variant across some set of features the model predicts.
By default, it is all the features, but you may pass in a function that accepts a `list(str)` of features and returns the `list(int)` of feature indices over which you want the max to be computed.
This is helpful if, for example, you only want to visualize the max probability difference scores for TF or DNase or histone features.

The first step is to parse the difference score file. `load_variant_abs_diff_scores` loads the variant absolute diff scores as a matrix and the variant labels and model features as lists:

In [4]:
from selene_sdk.interpret import load_variant_abs_diff_scores
from selene_sdk.interpret import variant_diffs_scatter_plot


dh_diffs, dh_labels, dh_features = load_variant_abs_diff_scores(
    os.path.join(variants_output_dir, "25k_example_variants_diffs.tsv"))

`variant_diffs_scatter_plot` is the method that generates the Manhattan plot using Plotly.
If your file is very large (over 100k variants), we recommend that you specify an `nth_percentile` value.
This means the plot would only display the variants with a max absolute difference score within the `nth_percentile` of scores.

If your variant coordinates are specified using either the reference genome hg19 or hg38, pass in `"hg19"` or `"hg38"` to the optional parameter `hg_reference_version`. Otherwise, `hg_reference_version` should be None. The method adds information about the nearest protein-coding gene for each variant based on the coordinates in Gencode, version 28. 

In [5]:
fig = variant_diffs_scatter_plot(
    dh_diffs, dh_labels, dh_features,
    os.path.join(variants_output_dir, "25k_example_variants.html"),  # output file path
    hg_reference_version="hg19",
    threshold_line=0.70,  # draws a horizontal line at `y=threshold_line`
    auto_open=False  # `auto_open=True` will open a new tab automatically with the HTML file.
)

In [6]:
iplot(fig)

## _In silico_ mutagenesis

For a more comprehensive tutorial on the visualization functions provided for _in silico_ mutagenesis, please refer to the tutorial [here](). This tutorial focuses on how to quickly use `AnalyzeSequences.in_silico_mutagenesis_from_file` to get the computed logit scores for every mutation and visualize the results for a feature-of-interest as a heatmap. We do not show how to visualize the motif plot in this example, but it is included in the more comprehensive tutorial. 

We will use the same `selene.predict.AnalyzeSequences` we initialized for variant effect prediction. The reference sequence version *does not* matter in this case since we are not working with genome coordinates. We only need to know that the sequence is type `selene.sequences.Genome`. This means the bases/alphabet available for us to mutate positions in a sequence is `['A', 'C', 'G', 'T']`. 

In [ ]:
ism_output_dir = os.path.join("data", "regulatory_mutations")
model_predict.in_silico_mutagenesis_from_file(
    "regulatory_mutations.fa",
    save_data=["logits"],
    output_dir=ism_output_dir
)

output_files = os.listdir(ism_output_dir)
print("Output filenames: {0}".format(output_files))

## Visualizing the logit scores for _in silico_ mutagenesis on 2 sequences centered at known regulatory mutations 

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

from selene_sdk.interpret import heatmap
from selene_sdk.interpret import ISMResult

For the first file, 'myo_infarc_LDL_CEBPB_T_to_G_mutation_logits.tsv', we are interested in visualizing any features containing the transcription factor CEBPB. 

Load the logit scores:

In [ ]:
known_CEBPB_mutation = ISMResult.from_file(
    os.path.join(ism_output_dir, "myo_infarc_LDL_CEBPB_T_to_G_mutation_logits.tsv"))

Here, we provide a `visualize` function. Within it, we use some helper functions (`_get_features_containing_str` and `_get_scores`) to visualize multiple heatmaps for features that contain the target substring:

In [ ]:
def _get_features_containing_str(feature_substring):
    features = []
    for feature in distinct_features:
        if feature_substring in feature:
            features.append(feature)
    return features

def _get_scores(ism_result, visualize_features, start, end):
    matrices = []
    for f in visualize_features:
        score_matrix = ism_result.get_score_matrix_for(f)
        matrices.append(score_matrix[start:end,])
    return matrices

def visualize(ism_result, target, start=400, end=600):
    """
    Parameters
    ----------
    ism_result : selene.interpret.ISMResult
        Output of `ISMResult.from_file` from an output file.
    target : str
        Pass in a feature name. If you want to visualize multiple features
        that share the same substring, pass in that substring.
    start : int
        Starting position for the heatmap visualization.
    end : int
        Ending position for the heatmap visualization.
    
    """
    target_features = _get_features_containing_str(target)
    matrices = _get_scores(ism_result, target_features, start, end)
    reference_encoding = Genome.sequence_to_encoding(
        ism_result.reference_sequence)[start:end,] == 1.
    for ix, m in enumerate(matrices):
        figure, (ax) = plt.subplots(1, 1, figsize=(24, 4))
        ax.patch.set(edgecolor="gray", hatch="//")
        ax.set_title("Feature {0}".format(target_features[ix]))
        
        # Set the min and max for the colorbar so that it is centered at 0.
        colorbar_bound = max(np.max(m), np.abs(np.min(m)))
        
        heatmap(m, mask=reference_encoding,
                cbar=True,
                cmap="bwr",
                vmin=-1 * colorbar_bound,
                vmax=colorbar_bound,
                ax=ax,
                linewidth=0.5,
                xticklabels=list(range(start, end)))

In [ ]:
visualize(known_CEBPB_mutation, "CEBPB")

For the second file, 'a_thalassemia_GATA1_T_to_C_mutation_logits.tsv', we are interested in visualizing any features containing the transcription factor GATA-1. 

In [ ]:
known_GATA1_mutation = ISMResult.from_file(
    os.path.join(ism_output_dir, "a_thalassemia_GATA1_T_to_C_mutation_logits.tsv"))

In [ ]:
visualize(known_GATA1_mutation, "GATA-1")